# Python Notebook

### Import libraries

In [39]:
import pandas as pd
import numpy as np

from sklearn.preprocessing import MinMaxScaler, StandardScaler, MaxAbsScaler, RobustScaler, QuantileTransformer, PowerTransformer, Normalizer
from sklearn.metrics import r2_score, mean_squared_error, mean_absolute_error

from sklearn.model_selection import cross_val_score, GridSearchCV
from sklearn.pipeline import make_pipeline, Pipeline
from lightgbm import LGBMRegressor

from sklearn.ensemble import BaggingRegressor, ExtraTreesRegressor, GradientBoostingRegressor, RandomForestRegressor

from sklearn.model_selection import cross_val_score, KFold, GridSearchCV, train_test_split

### Function

In [40]:
def drop_data(df, drop_list):
    """
    Dropping the features of the drop_list from the df
    
    Parameters
    ----------
    Input:
        df: The Dataframe
        drop_list: The list of features to drop from the df
        
        Return
    ----------
    Output:
        dropped_df: The Dataframe with the selected features dropped
    """
    dropped_df = df.drop(columns=drop_list)
    return dropped_df


def sanity_check (X_train, Y_train, X_test, Y_test):
    """
    Checking the shapes of the train and test sets 
    
    Parameters
    ----------
    Input:
        All the sets we need
        
    Return
    ----------
    Output:
        Printing the shapes to check that everything is great
    """
    print ('Shape of X_train=>',X_train.shape)
    print ('Shape of X_test=>',X_test.shape)
    print ('Shape of Y_train=>',Y_train.shape)
    print ('Shape of Y_test=>',Y_test.shape)


def scaling_the_train_data(scaler, X_train):
    """
    Scaling the training data and train the scaler for the test data
    
    Parameters
    ----------
    Input:
        scaler: Library fucntion
            The scaler we want to use
        X_train: Numpy array
            The training data we will scale
            
    Return
    ----------
    Output:
        X_train: Numpy array
            The training features but scaled
        scaler: Library fucntion
            The scaler but trained
    """
    print(f'The scaler: {scaler}')
    X_train = scaler.fit_transform(X_train)
    trained_scaler = scaler
    return trained_scaler, X_train


def scaling_the_test(scaler, X_test):
    """

    Parameters
    ----------
    Input:
        scaler : class object
            The scaler used to scale the test data
        X_test : Numpy array
            The test set that we will scale

    Returns
    ----------
    X_test: Numpy array
        The test set but scaled 
    
    """
    X_test = scaler.transform(X_test)
    return X_test


def train_the_model(model, X_train, Y_train, cv, scoring):
    """
    Training of a specific model
    
    Parameters
    ----------
    Input:
        model: Name of the model
        X_train: The input features of the models
        Y_train: The target of the model
        cv: Number of subsets that the data will be splitted
        scoring: The metric that the cross validation with use
        
    Returns
    ----------
    Output:
        model: Trained model
    """
    # Cross validation of the training set
    cross_val = cross_val_score(model, X_train, Y_train, cv=cv, scoring=scoring)
    print (f'The mean of the cross validation: {(-1)*np.mean(cross_val)}')
    print (f'The root of the mean of the cross validation: {np.sqrt((-1)*np.mean(cross_val))}')
    
    # Training the model
    trained_model = model
    model.fit(X_train, Y_train)
    pred_train = model.predict(X_train)
    print (f'The prediction of the model on the training set has R2 score: {r2_score(Y_train, pred_train)}, MSE: {mean_squared_error(Y_train, pred_train)}')
    
    return trained_model


def predictions (model, X_test):
    """
    Parameters
    ----------
    model : Regressor
        The trained model that will predict the test set
        
    X_test : Numpy array
        The test set that to predict the target

    Returns
    ----------
    pred : Numpy array
        The prediction from the test set
    """
    pred = model.predict(X_test)
    return pred


def acc_of_model(predicted, Y_test, model):
    """
    Parameters
    ----------
    predicted : Numpy array
        The predictions of the model
        
    Y_test : Numpy array
        The true labels of the test set
       
    model : Object of library
        The model we used

    Returns
    ---------
    Printing all the accuracies we want
    """
    print(f'The model is: {model}')
    print(f'The R2 accuracy of the model is: {r2_score(Y_test, predicted)}')
    print(f'The Mean Squared Error is: {mean_squared_error(Y_test, predicted)}')
    print(f'The Root of the Mean Squared Error is: {np.sqrt(mean_squared_error(Y_test, predicted))}')
    print(f'The Mean Absolute Error is: {mean_absolute_error(Y_test, predicted)}\n\n')

### Main

In [41]:
# Reading data 

path = '/home/mav24/Documents/Development/Regeneration/Project/Data/data_for_scaling.xlsx'
data = pd.read_excel(path)

In [42]:
# Dropping features we will not use

drop = ['Unnamed: 0', 'station wagon', 'diesel', 'total cc', 'encoded origin']
data = drop_data(data, drop)

In [43]:
# Splitting to training and testing data
X_train, X_test, Y_train, Y_test = train_test_split(data.drop(columns='mpg'), data['mpg'], test_size=0.2, random_state=13)

In [44]:
# Sanity check
sanity_check(X_train, Y_train, X_test, Y_test)

Shape of X_train=> (324, 7)
Shape of X_test=> (82, 7)
Shape of Y_train=> (324,)
Shape of Y_test=> (82,)


In [45]:
# Getting a list with all the features
cols = data.drop(columns='mpg').columns.tolist()

In [46]:
# Scaling and training the scaler on training data
scaler = Normalizer()
scaler_trained, X_train = scaling_the_train_data(scaler, X_train)

The scaler: Normalizer()


In [47]:
# Scaling the test data
X_test = scaling_the_test(scaler_trained, X_test)

In [48]:
# ExtraTreesRegressor
etr = ExtraTreesRegressor()
ert_trained = train_the_model(etr, X_train, Y_train, 10, 'neg_mean_squared_error')
pred_test = predictions(ert_trained, X_test)
acc_of_model(pred_test, Y_test, etr)
etr_importances = dict(zip(cols, ert_trained.feature_importances_))
print(f'Feature importances:\n{etr_importances}')

The mean of the cross validation: 7.967325358370275
The root of the mean of the cross validation: 2.8226450996131756
The prediction of the model on the training set has R2 score: 0.9999999589017889, MSE: 2.4691358024690304e-06
The model is: ExtraTreesRegressor()
The R2 accuracy of the model is: 0.8679433629781171
The Mean Squared Error is: 8.645372359213226
The Root of the Mean Squared Error is: 2.9403014061849553
The Mean Absolute Error is: 2.1867354274611293


Feature importances:
{'cylinders': 0.040600895597243114, 'displacements': 0.15920154153486016, 'horsepower': 0.027468505255206544, 'weight': 0.06776003179483281, 'acceleration': 0.22658960611053142, 'encoded car brand': 0.11963868579768004, 'encoded model year': 0.358740733909646}


In [49]:
# BaggingRegressor
bgr = BaggingRegressor()
bgr_trained = train_the_model(bgr, X_train, Y_train, 10, 'neg_mean_squared_error')
pred_test = predictions(bgr_trained, X_test)
acc_of_model(pred_test, Y_test, bgr)
#bgr_importances = dict(zip(cols, bgr_trained.feature_importances_))
#print(f'Feature importances:\n{bgr_importances}')

The mean of the cross validation: 9.304492839474703
The root of the mean of the cross validation: 3.050326677501068
The prediction of the model on the training set has R2 score: 0.9713735002308479, MSE: 1.719848959067216
The model is: BaggingRegressor()
The R2 accuracy of the model is: 0.8443121253232784
The Mean Squared Error is: 10.192442263782183
The Root of the Mean Squared Error is: 3.192560455775612
The Mean Absolute Error is: 2.3963345487353274




In [50]:
# GradientBoostingRegressor
gbr = GradientBoostingRegressor()
gbr_trained = train_the_model(gbr, X_train, Y_train, 10, 'neg_mean_squared_error')
pred_test = predictions(gbr_trained, X_test)
acc_of_model(pred_test, Y_test, gbr)
gbr_importances = dict(zip(cols, gbr_trained.feature_importances_))
print(f'Feature importances:\n{gbr_importances}')

The mean of the cross validation: 9.069928575328921
The root of the mean of the cross validation: 3.0116322111653875
The prediction of the model on the training set has R2 score: 0.9752147207664819, MSE: 1.4890726087263784
The model is: GradientBoostingRegressor()
The R2 accuracy of the model is: 0.8565115153555551
The Mean Squared Error is: 9.39378290244444
The Root of the Mean Squared Error is: 3.0649278788324597
The Mean Absolute Error is: 2.244757616807856


Feature importances:
{'cylinders': 0.046039162668968285, 'displacements': 0.36621317028312034, 'horsepower': 0.014828758487664634, 'weight': 0.017000900395490265, 'acceleration': 0.252711393784376, 'encoded car brand': 0.0564107907504258, 'encoded model year': 0.2467958236299547}


In [51]:
# RandomForestRegressor
rfr = RandomForestRegressor()
rfr_trained = train_the_model(rfr, X_train, Y_train, 10, 'neg_mean_squared_error')
pred_test = predictions(rfr_trained, X_test)
acc_of_model(pred_test, Y_test, rfr)
rfr_importances = dict(zip(cols, rfr_trained.feature_importances_))
print(f'Feature importances:\n{rfr_importances}')

The mean of the cross validation: 8.543432911101922
The root of the mean of the cross validation: 2.922915139223498
The prediction of the model on the training set has R2 score: 0.9801684359425991, MSE: 1.1914587908351195
The model is: RandomForestRegressor()
The R2 accuracy of the model is: 0.8590507733875516
The Mean Squared Error is: 9.227544902614905
The Root of the Mean Squared Error is: 3.0376874267466865
The Mean Absolute Error is: 2.2997286495579488


Feature importances:
{'cylinders': 0.047216446094684617, 'displacements': 0.36388072541547906, 'horsepower': 0.016731680188229448, 'weight': 0.023560544830762677, 'acceleration': 0.1923226110221769, 'encoded car brand': 0.048659674833041865, 'encoded model year': 0.3076283176156254}


In [52]:
# LightGBM
lgb = LGBMRegressor()
lgb_trained = train_the_model(lgb, X_train, Y_train, 10, 'neg_mean_squared_error')
pred_test = predictions(lgb_trained, X_test)
acc_of_model(pred_test, Y_test, lgb)
lgb_importances = dict(zip(cols, lgb_trained.feature_importances_))
print(f'Feature importances:\n{lgb_importances}')

The mean of the cross validation: 9.104201483913661
The root of the mean of the cross validation: 3.0173169346148674
The prediction of the model on the training set has R2 score: 0.970828084203007, MSE: 1.752616960579978
The model is: LGBMRegressor()
The R2 accuracy of the model is: 0.8631388402258239
The Mean Squared Error is: 8.959910796194658
The Root of the Mean Squared Error is: 2.993311008932192
The Mean Absolute Error is: 2.321769087055778


Feature importances:
{'cylinders': 184, 'displacements': 125, 'horsepower': 117, 'weight': 115, 'acceleration': 217, 'encoded car brand': 171, 'encoded model year': 234}


### Feature Tunning of every model

In [53]:
# ExtraTreesRegressor

model = ExtraTreesRegressor()

param_grid = {'n_estimators': [10,50,100],
              'criterion': ['mse', 'mae'],
              'max_depth': [2,8,16,32,50],
              #'min_sample_split': [2,4,6],
              #'min_sample_leaf': [2, 4],
              #'oob_score': [True, False],
              'max_features': ['auto','sqrt','log2'],    
              'bootstrap': [True, False],
              'warm_start': [True, False],
              }

gcv = GridSearchCV(model,param_grid,cv=10,scoring='neg_mean_squared_error').fit(X_train, Y_train)
print(f'Model name: {model}')
print(f'The best score is: {gcv.best_score_}')
print(f'The best parameters are: {gcv.best_params_}')
print(f'The best estimators are: {gcv.best_estimator_}')

model_tuned = ExtraTreesRegressor(n_estimators=100, 
                                  bootstrap=False, 
                                  criterion='mse', 
                                  max_depth=32, 
                                  max_features='auto', 
                                  warm_start=False)

model_trained = train_the_model(model_tuned, X_train, Y_train, 10, 'neg_mean_squared_error')
pred_test_tuned = predictions(model_trained, X_test)
acc_of_model(pred_test_tuned, Y_test, model_tuned)

Model name: ExtraTreesRegressor()
The best score is: -7.735210097119318
The best parameters are: {'bootstrap': False, 'criterion': 'mae', 'max_depth': 8, 'max_features': 'auto', 'n_estimators': 50, 'warm_start': True}
The best estimators are: ExtraTreesRegressor(criterion='mae', max_depth=8, n_estimators=50,
                    warm_start=True)
The mean of the cross validation: 7.929899297145125
The root of the mean of the cross validation: 2.816007687692831
The prediction of the model on the training set has R2 score: 0.9999999178035779, MSE: 4.938271604938937e-06
The model is: ExtraTreesRegressor(max_depth=32)
The R2 accuracy of the model is: 0.8646164908813154
The Mean Squared Error is: 8.86317321130945
The Root of the Mean Squared Error is: 2.9771081961039725
The Mean Absolute Error is: 2.264929913807422




In [ ]:
# RandomForestRegressor

rfr = RandomForestRegressor()

param_grid = {
              'n_estimators': [1,2,5,10,20,50,100,200, 500],
              'max_depth' : [0, 1, 2, 5, 10],
              'max_features': ['auto','sqrt','log2'],
              'max_samples': [1,2,8,16,32,50],  
              'bootstrap': [True, False],
              'warm_start': [True, False],
              'random_state' : [13, 42]
              }

gcv = GridSearchCV(rfr,param_grid,cv=10,scoring='neg_mean_squared_error').fit(X_train, Y_train)

print(f'Model name: {rfr}')
print(f'The best score is: {gcv.best_score_}')
print(f'The best parameters are: {gcv.best_params_}')
print(f'The best estimators are: {gcv.best_estimator_}')

model_tuned = RandomForestRegressor(bootstrap=False,
                            max_depth=10,
                            max_features='sqrt',
                            max_samples=1,
                            n_estimators=200,
                            random_state=42,
                            warm_start=True)

model_trained = train_the_model(model_tuned, X_train, Y_train, 10, 'neg_mean_squared_error')
pred_test_tuned = predictions(model_trained, X_test)
acc_of_model(pred_test_tuned, Y_test, model_tuned)

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

...

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:615: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 598, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/sklearn/ensemble/_forest.py", line 387, in fit
    trees = Parallel(n_jobs=self.n_jobs, verbose=self.verbose,
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 1041, in __call__
    if self.dispatch_one_batch(iterator):
  File "/home/mav24/anaconda3/envs/PythonTest/lib/python3.8/site-packages/joblib/parallel.py", line 859, in dispatch_one_batch
    self._dispatch(tasks)
  File "/home/mav24/anaconda3/envs/

In [ ]:
# LightGBM

lgb = LGBMRegressor()

param_grid = {'boosting_type' : ['gbdt', 'dart', 'goss', 'rf'],
              'num_leaves' : [2,5,10,15,20,25,31,40],
              'max_depth' : [-1, 1, 2, 5, 10, 20, 50],
              'n_estimators' : [40, 50, 100, 150, 200],
              }

gcv = GridSearchCV(lgb,param_grid,cv=10,scoring='neg_mean_squared_error').fit(X_train, Y_train)

print(f'Model name: {lgb}')
print(f'The best score is: {gcv.best_score_}')
print(f'The best parameters are: {gcv.best_params_}')
print(f'The best estimators are: {gcv.best_estimator_}')

model_tuned = LGBMRegressor(boosting_type='gbdt',
                            max_depth=-1,
                            n_estimators=100,
                            num_leaves=5)
model_trained = train_the_model(model_tuned, X_train, Y_train, 10, 'neg_mean_squared_error')
pred_test_tuned = predictions(model_trained, X_test)
acc_of_model(pred_test_tuned, Y_test, model_tuned)